In [14]:
from sympy import * 
import re
from sympy.functions import Abs
from IPython.display import display

errors = []

def fl_op(a,b,op,e):
    return op(a,b)*(1 + e)

def fl_add(a,b):
    # Append an addition error to the global list of errors
    errors.append(symbols("e" + str(len(errors)+1)))
    return fl_op(a,b, lambda x,y : x + y, errors[-1]) 

def fl_sub(a,b):
    # Append an addition error to the global list of errors
    errors.append(symbols("e" + str(len(errors)+1)))
    return fl_op(a,b, lambda x,y : x - y, errors[-1]) 

def fl_mul(a,b):
    # Append an addition error to the global list of errors
    errors.append(symbols("e" + str(len(errors)+1)))
    return fl_op(a,b, lambda x,y : x * y, errors[-1]) 

def fl_div(a,b):
    # Append an addition error to the global list of errors
    errors.append(symbols("e" + str(len(errors)+1)))
    return fl_op(a,b, lambda x,y : x / y, errors[-1]) 

def fl_vsub(va,vb):
    assert (len(va) == len(vb))
    return [fl_sub(va[i],vb[i]) for i in range(len(va))]

def fl_vadd(va,vb):
    assert (len(va) == len(vb))
    return [fl_add(va[i],vb[i]) for i in range(len(va))]

def fl_vsum(va):
    return fl_add(fl_add(va[0],va[1]),va[2])

def fl_dot(va,vb):
    assert (len(va) == len(vb))
    return fl_vsum([fl_mul(va[i],vb[i]) for i in range(len(va))])

def filter_error_products(inputStr):
    inputStr = str(inputStr)
    resultStr = re.sub("(e\d+\*){2,}",'del', inputStr)
    resultStr = re.sub("\s*[+-]*del[nprq]_\d+\*[nprq]_\d+\s*[+-]*",'', resultStr)
    return sympify(resultStr)

def clean_up_error(errorExpression):
    errorExpression = expand(errorExpression)
    errorExpression = filter_error_products(errorExpression)
    errorExpression = factor(errorExpression, errors)
    return errorExpression 

def clean_up_error(errorExpression):
    errorExpression = expand(errorExpression)
    errorExpression = filter_error_products(errorExpression)
    errorExpression = factor(errorExpression, errors)
    return errorExpression 

In [23]:
p0,p1,p2 = symbols("p_0:3")
q0,q1,q2 = symbols("q_0:3")
r0,r1,r2 = symbols("r_0:3")
n0,n1,n2 = symbols("n_0:3")

components = [p0,p1,p2,q0,q1,q2,r0,r1,r2,n0,n1,n2]

p = Matrix([p0,p1,p2])
q = Matrix([q0,q1,q2])
r = Matrix([r0,r1,r2])
n = Matrix([n0,n1,n2])

errors = []

distFloat = fl_dot(fl_sub(r,p),n)
distExact = (r-p).dot(n)
distError = distFloat - distExact 
distError = clean_up_error(distError)
distError = distError.factor(errors)

print ("Distance error")
display(distError)
print_latex(distError)

Distance error


e1*(n_0*p_0 + n_0*r_0 - n_1*p_1 + n_1*r_1 - n_2*p_2 + n_2*r_2) + e2*(-n_0*p_0 + n_0*r_0) + e3*(-n_1*p_1 + n_1*r_1) + e4*(-n_2*p_2 + n_2*r_2) + e5*(-n_0*p_0 + n_0*r_0 - n_1*p_1 + n_1*r_1) + e6*(-n_0*p_0 + n_0*r_0 - n_1*p_1 + n_1*r_1 - n_2*p_2 + n_2*r_2)

e_{1} \left(n_{0} p_{0} + n_{0} r_{0} - n_{1} p_{1} + n_{1} r_{1} - n_{2} p_{2} + n_{2} r_{2}\right) + e_{2} \left(- n_{0} p_{0} + n_{0} r_{0}\right) + e_{3} \left(- n_{1} p_{1} + n_{1} r_{1}\right) + e_{4} \left(- n_{2} p_{2} + n_{2} r_{2}\right) + e_{5} \left(- n_{0} p_{0} + n_{0} r_{0} - n_{1} p_{1} + n_{1} r_{1}\right) + e_{6} \left(- n_{0} p_{0} + n_{0} r_{0} - n_{1} p_{1} + n_{1} r_{1} - n_{2} p_{2} + n_{2} r_{2}\right)


At this point the triangle inequality can be applied

$$\left|\sum_{i=1}^6 e_i \cdot E_i \right| \le \sum_{i=1}^6 |e_i| \cdot |E_i|  $$

and the error is factorized for $e_i$ 

In [18]:
distErrorDiffs = [diff(distError, error) for error in errors]
pprint (distErrorDiffs)

[n₀⋅p₀ + n₀⋅r₀ - n₁⋅p₁ + n₁⋅r₁ - n₂⋅p₂ + n₂⋅r₂, -n₀⋅p₀ + n₀⋅r₀, -n₁⋅p₁ + n₁⋅r₁
, -n₂⋅p₂ + n₂⋅r₂, -n₀⋅p₀ + n₀⋅r₀ - n₁⋅p₁ + n₁⋅r₁, -n₀⋅p₀ + n₀⋅r₀ - n₁⋅p₁ + n₁⋅
r₁ - n₂⋅p₂ + n₂⋅r₂]


In [19]:
distErrorMult = [Abs(distErrorDiffs[i]) * Abs(errors[i]) for i in range(len(errors))]
pprint (distErrorMult)

[│e₁│⋅│n₀⋅p₀ + n₀⋅r₀ - n₁⋅p₁ + n₁⋅r₁ - n₂⋅p₂ + n₂⋅r₂│, │e₂│⋅│n₀⋅p₀ - n₀⋅r₀│, │
e₃│⋅│n₁⋅p₁ - n₁⋅r₁│, │e₄│⋅│n₂⋅p₂ - n₂⋅r₂│, │e₅│⋅│n₀⋅p₀ - n₀⋅r₀ + n₁⋅p₁ - n₁⋅r₁
│, │e₆│⋅│n₀⋅p₀ - n₀⋅r₀ + n₁⋅p₁ - n₁⋅r₁ + n₂⋅p₂ - n₂⋅r₂│]


In [20]:
distErrorAbs = sum(distErrorMult)
display(distErrorAbs)

Abs(e1)*Abs(n_0*p_0 + n_0*r_0 - n_1*p_1 + n_1*r_1 - n_2*p_2 + n_2*r_2) + Abs(e2)*Abs(n_0*p_0 - n_0*r_0) + Abs(e3)*Abs(n_1*p_1 - n_1*r_1) + Abs(e4)*Abs(n_2*p_2 - n_2*r_2) + Abs(e5)*Abs(n_0*p_0 - n_0*r_0 + n_1*p_1 - n_1*r_1) + Abs(e6)*Abs(n_0*p_0 - n_0*r_0 + n_1*p_1 - n_1*r_1 + n_2*p_2 - n_2*r_2)

Assuming the substitution with the unit roundoff

$$|e_i| \le 0.5 \epsilon, \epsilon = 2^{-p + 1}$$

leads to 

In [22]:
epsilonDict = {}

epsilon = symbols("epsilon")

# Standard floating point model.
for error in errors:
    epsilonDict[Abs(error)] = 0.5*epsilon
    
distErrorEps = factor(distErrorAbs.subs(epsilonDict), epsilon)
display(distErrorEps)

0.5*epsilon*(Abs(n_0*p_0 - n_0*r_0) + Abs(n_1*p_1 - n_1*r_1) + Abs(n_2*p_2 - n_2*r_2) + Abs(n_0*p_0 - n_0*r_0 + n_1*p_1 - n_1*r_1) + Abs(n_0*p_0 - n_0*r_0 + n_1*p_1 - n_1*r_1 + n_2*p_2 - n_2*r_2) + Abs(n_0*p_0 + n_0*r_0 - n_1*p_1 + n_1*r_1 - n_2*p_2 + n_2*r_2))

$e_r = 0.5 \cdot \epsilon \cdot (|n_0 \cdot (p_0 - r_0)| + |n_1 \cdot (p_1 - r_1)| + |n_2 \cdot (p_2 - r_2)| + |n_0 \cdot (p_0 - r_0) + n_1 \cdot (p_1 - r_1)| + |n \cdot (p - r)| + |n_0 \cdot p_0  + n_0 \cdot r_0 - n1\cdot(p_1 - r_1) - n_2 \cdot(p_2 - r_2)|$ 

$n \cdot (p - r)$ could be minimized in the $L_2$ and $L_1$ norm. The closer the points $p,r$ are, the smaller the error will be, irrespective of the normal $n$ orientation. The errror will increase with the magnitude of the normal $n$ components. There could be a problem with cancellation if p is very near to r.  